In [3]:
import os
os.environ["TF_XLA_FLAGS"] = "--tf_xla_auto_jit=0"   # отключить XLA autoclustering [web:48]
os.environ["XLA_FLAGS"] = "--xla_gpu_autotune_level=0"
os.environ["TF_CPP_MIN_LOG_LEVEL"] = "3"            
os.chdir("/home/konnilol/Documents/uni/mmo/pr7")

import numpy as np
import pandas as pd

from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, RobustScaler
from sklearn.impute import SimpleImputer
from sklearn.pipeline import Pipeline
from sklearn.mixture import GaussianMixture
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score, davies_bouldin_score, calinski_harabasz_score

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
tf.config.optimizer.set_jit(False)


In [4]:
# -----------------------------
# 1) Load
# -----------------------------
df = pd.read_csv("penguins.csv")
df = df.replace("NA", np.nan)

num_cols = ["culmen_length_mm", "culmen_depth_mm", "flipper_length_mm", "body_mass_g"]
cat_cols = ["sex"]

for c in num_cols:
    df[c] = pd.to_numeric(df[c], errors="coerce")

# отфильтровать явно невозможные значения (минимум)
df = df[(df["flipper_length_mm"].isna()) | ((df["flipper_length_mm"] > 0) & (df["flipper_length_mm"] < 300))]

# квантильная обрезка по всем числам
for c in num_cols:
    lo, hi = df[c].quantile([0.01, 0.99])
    df = df[(df[c].isna()) | ((df[c] >= lo) & (df[c] <= hi))]

X = df[num_cols + cat_cols].copy()


In [5]:
# -----------------------------
# 2) Preprocess
# -----------------------------
num_pipe = Pipeline(steps=[
    ("imputer", SimpleImputer(strategy="median")),
    ("scaler", RobustScaler(quantile_range=(10, 90))),
])

cat_pipe = Pipeline(steps=[
    ("imputer", SimpleImputer(strategy="most_frequent")),
    ("onehot", OneHotEncoder(handle_unknown="ignore", sparse_output=False)),
])

preprocess = ColumnTransformer(
    transformers=[
        ("num", num_pipe, num_cols),
        ("cat", cat_pipe, cat_cols),
    ],
    remainder="drop"
)

X_proc = preprocess.fit_transform(X).astype("float32")
in_dim = X_proc.shape[1]



In [6]:
# -----------------------------
# 3) Autoencoder (Keras)
# -----------------------------
latent_dim = 3  # попробуй 2..10

inp = keras.Input(shape=(in_dim,))
x = layers.Dense(64, activation="relu")(inp)
x = layers.Dropout(0.1)(x)
x = layers.Dense(32, activation="relu")(x)
z = layers.Dense(latent_dim, name="z")(x)

x = layers.Dense(32, activation="relu")(z)
x = layers.Dense(64, activation="relu")(x)
out = layers.Dense(in_dim, name="recon")(x)

autoencoder = keras.Model(inp, out)
encoder = keras.Model(inp, z)

autoencoder.compile(
    optimizer=keras.optimizers.Adam(1e-3),
    loss="mse",
)

cb = [
    keras.callbacks.EarlyStopping(monitor="val_loss", patience=30, restore_best_weights=True)
]

autoencoder.fit(
    X_proc, X_proc,
    validation_split=0.2,
    epochs=400,
    batch_size=128,
    shuffle=True,
    callbacks=cb,
    verbose=0
)

Z = encoder.predict(X_proc, batch_size=512, verbose=0)



I0000 00:00:1766514729.133869  267477 gpu_device.cc:2020] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 1050 MB memory:  -> device: 0, name: NVIDIA GeForce RTX 3080, pci bus id: 0000:06:00.0, compute capability: 8.6
I0000 00:00:1766514731.744964  268281 device_compiler.h:196] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


In [7]:
# -----------------------------
# 4) GMM + BIC choose K
# -----------------------------
def gmm_select_bic(Z, k_min=1, k_max=10, covariance_type="full", seed=42):
    best_gmm = None
    best_bic = np.inf
    bics = []

    for k in range(k_min, k_max + 1):
        gmm = GaussianMixture(
            n_components=k,
            covariance_type=covariance_type,
            random_state=seed,
            reg_covar=1e-5,
            n_init=10,
            init_params="kmeans",
        )
        gmm.fit(Z)
        bic = gmm.bic(Z)  # lower is better [web:29]
        bics.append((k, float(bic)))
        if bic < best_bic:
            best_bic = bic
            best_gmm = gmm

    return best_gmm, bics

best_gmm, bics = gmm_select_bic(Z, k_min=1, k_max=10, covariance_type="full")
labels_seq = best_gmm.predict(Z)
K_seq = int(best_gmm.n_components)

def safe_silhouette(Z, y):
    if len(np.unique(y)) < 2:
        return np.nan
    return float(silhouette_score(Z, y))

metrics_seq = {
    "K_by_BIC": K_seq,
    "silhouette(Z)": safe_silhouette(Z, labels_seq),
    "davies_bouldin(Z)": float(davies_bouldin_score(Z, labels_seq)) if len(np.unique(labels_seq)) > 1 else np.nan,
    "calinski_harabasz(Z)": float(calinski_harabasz_score(Z, labels_seq)) if len(np.unique(labels_seq)) > 1 else np.nan,
}

print("BICs:", bics)
print("Sequential AE -> GMM metrics:", metrics_seq)


BICs: [(1, 1845.0574170856535), (2, 1255.4345240997866), (3, 928.4383567875949), (4, 671.30694117199), (5, 588.6201160653229), (6, 578.1610481741557), (7, 615.900985827174), (8, 650.4230662981665), (9, 685.973753839605), (10, 727.855346997327)]
Sequential AE -> GMM metrics: {'K_by_BIC': 6, 'silhouette(Z)': 0.6100717186927795, 'davies_bouldin(Z)': 0.565238385936235, 'calinski_harabasz(Z)': 891.8729026062824}


In [8]:
# -----------------------------
# 1) Init cluster centers by KMeans on Z
# -----------------------------
kmeans = KMeans(n_clusters=K_seq, n_init=50, random_state=42)
y0 = kmeans.fit_predict(Z)
centers0 = kmeans.cluster_centers_.astype("float32")


In [9]:
# -----------------------------
# 2) Build DEC model (no custom Layer class; use tf.Variable + Lambda)
# -----------------------------
alpha = 1.0
mu = tf.Variable(centers0, trainable=True, name="cluster_centers")  # (K, latent_dim)

inp = keras.Input(shape=(in_dim,), name="x")

# reuse encoder part by calling encoder on inp
z = encoder(inp)

# Student-t soft assignment q (DEC) [web:18]
def soft_q(args):
    z_batch, mu_var = args  # z: (B, d), mu: (K, d)
    # dist^2: (B, K)
    z_exp = tf.expand_dims(z_batch, axis=1)
    mu_exp = tf.expand_dims(mu_var, axis=0)
    dist_sq = tf.reduce_sum(tf.square(z_exp - mu_exp), axis=2)
    q = 1.0 / (1.0 + dist_sq / alpha)
    q = tf.pow(q, (alpha + 1.0) / 2.0)
    q = q / tf.reduce_sum(q, axis=1, keepdims=True)
    return q

q = layers.Lambda(soft_q, name="q")([z, mu])

# reconstruction head from latent z: reuse decoder part by calling autoencoder? проще собрать декодер заново:
# (чтобы было линейно, делаем новый декодер, инициализируем весами из autoencoder по совпадающим слоям при желании)
x = layers.Dense(32, activation="relu")(z)
x = layers.Dense(64, activation="relu")(x)
recon = layers.Dense(in_dim, name="recon")(x)

dec_model = keras.Model(inp, outputs=[recon, q], name="DEC_joint")


In [10]:
# -----------------------------
# 3) Losses: reconstruction + KL(P||Q)
# -----------------------------
lambda_rec = 1.0
lambda_kl = 0.2

mse = keras.losses.MeanSquaredError()

def kl_pq(p, q):
    # KL(P || Q) [web:18]
    p = tf.clip_by_value(p, 1e-10, 1.0)
    q = tf.clip_by_value(q, 1e-10, 1.0)
    return tf.reduce_mean(tf.reduce_sum(p * tf.math.log(p / q), axis=1))

optimizer = keras.optimizers.Adam(1e-4)


In [11]:
# -----------------------------
# 4) Training loop 
# -----------------------------
X_tf = tf.convert_to_tensor(X_proc, dtype=tf.float32)

batch_size = 128
dataset = tf.data.Dataset.from_tensor_slices(X_tf).shuffle(len(X_proc), seed=42).batch(batch_size)

def target_distribution(q_np):
    # p_ij = (q_ij^2 / f_j) / sum_j(...)
    weight = (q_np ** 2) / np.sum(q_np, axis=0, keepdims=True)
    p = weight / np.sum(weight, axis=1, keepdims=True)
    return p.astype("float32")

update_interval = 5
max_epochs = 200

for epoch in range(1, max_epochs + 1):
    # обновляем P периодически
    if epoch == 1 or epoch % update_interval == 0:
        _, q_all = dec_model.predict(X_proc, batch_size=512, verbose=0)
        P_all = target_distribution(q_all)

    # один проход по батчам
    idx = 0
    losses = []
    for xb in dataset:
        b = xb.shape[0]
        p_batch = tf.convert_to_tensor(P_all[idx:idx+b], dtype=tf.float32)
        idx += b

        with tf.GradientTape() as tape:
            recon_b, q_b = dec_model(xb, training=True)
            loss_rec = mse(xb, recon_b)
            loss_kl = kl_pq(p_batch, q_b)
            loss = lambda_rec * loss_rec + lambda_kl * loss_kl

        grads = tape.gradient(loss, dec_model.trainable_variables + [mu])
        optimizer.apply_gradients(zip(grads, dec_model.trainable_variables + [mu]))
        losses.append(float(loss.numpy()))

    if epoch % 20 == 0:
        print(f"epoch={epoch} loss={np.mean(losses):.6f}")


epoch=20 loss=0.369318
epoch=40 loss=0.285631
epoch=60 loss=0.219172
epoch=80 loss=0.168555
epoch=100 loss=0.130258
epoch=120 loss=0.103850
epoch=140 loss=0.085708
epoch=160 loss=0.069362
epoch=180 loss=0.052419
epoch=200 loss=0.040367


In [12]:
# -----------------------------
# 5) Final labels + metrics
# -----------------------------
Z_final = encoder.predict(X_proc, batch_size=512, verbose=0)
_, q_final = dec_model.predict(X_proc, batch_size=512, verbose=0)
labels_dec = q_final.argmax(axis=1)

def safe_silhouette(Z, y):
    if len(np.unique(y)) < 2:
        return np.nan
    return float(silhouette_score(Z, y))

metrics_dec = {
    "K_used": int(K_seq),
    "silhouette(Z_final)": safe_silhouette(Z_final, labels_dec),
    "davies_bouldin(Z_final)": float(davies_bouldin_score(Z_final, labels_dec)) if len(np.unique(labels_dec)) > 1 else np.nan,
    "calinski_harabasz(Z_final)": float(calinski_harabasz_score(Z_final, labels_dec)) if len(np.unique(labels_dec)) > 1 else np.nan,
}

print("DEC metrics:", metrics_dec)


DEC metrics: {'K_used': 6, 'silhouette(Z_final)': -0.014072454534471035, 'davies_bouldin(Z_final)': 1.1342428506359734, 'calinski_harabasz(Z_final)': 77.43459746763591}


### Вывод: Обе схемы (последовательная AE→GMM+BIC и совместная DEC) на этих данных показали ограниченную эффективность автоматического выбора кластеров: критерий BIC у GMM выбирал избыточное число компонент, поэтому итоговая кластеризация не совпадает 2 группами по полу. При этом совместная схема DEC ухудшила качество по внутренним метрикам еще больше.